In [10]:
import pandas as pd 
import numpy as np
# import matplotlib.pyplot as plt
from tqdm import tqdm

# import cufflinks as cf
# from plotly import __version__
# from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot

# cf.go_offline()

# %matplotlib inline
from sklearn.metrics import mean_absolute_error, mean_absolute_percentage_error, mean_squared_error

from neuralforecast.auto import AutoLSTM, AutoRNN
from neuralforecast.tsdataset import TimeSeriesDataset
from neuralforecast.core import NeuralForecast
from neuralforecast.models import RNN

from datetime import datetime, timedelta
# import plotly.graph_objects as go
# import matplotlib.colors as mcolors
from neuralforecast.losses.pytorch import MQLoss
from tqdm import tqdm

In [11]:
# Load and process the MEASLES_ARIZONA data
df = pd.read_csv("../outbreaks_disease_location.csv")
value_columns = [str(i) for i in range(60)]
series_values = df[value_columns].fillna(0).astype(float)
start_dates = pd.to_datetime(df["start_date"])

# Shuffle and split
shuffled_indices = df.sample(frac=1, random_state=42).index
split_point = int(0.8 * len(df))
train_indices = shuffled_indices[:split_point]
test_indices = shuffled_indices[split_point:]

In [12]:
train_records = []
for i, row in series_values.iloc[train_indices].iterrows():
    dates = pd.date_range(start="2000-01-01", periods=60, freq="W-SAT")
    for t, value in enumerate(row):
        train_records.append({"unique_id": f"Y{i+1}", "ds": dates[t], "y": value})
df_train = pd.DataFrame(train_records)

test_start_dates = start_dates.loc[test_indices] - pd.Timedelta(weeks=4)
df_test_all = []

for idx in test_indices:
    start_date = test_start_dates.loc[idx]
    row = series_values.loc[idx]
    dates = pd.date_range(start=start_date, periods=60, freq="W-SAT")
    for t, value in enumerate(row):
        df_test_all.append({"unique_id": f"Y_{idx}", "ds": dates[t], "y": value})

df_test_all = pd.DataFrame(df_test_all)

In [13]:
df_train["date"] = pd.to_datetime(df_train["ds"])
df_train.set_index("date", inplace = True)

df_test_all["date"] = pd.to_datetime(df_test_all["ds"])
df_test_all.set_index("date", inplace = True)

In [14]:
df_test_all

unique_id         ds        y
date                                    
2022-08-13    Y_5607 2022-08-13  20775.0
2022-08-20    Y_5607 2022-08-20  16570.0
2022-08-27    Y_5607 2022-08-27  13995.0
2022-09-03    Y_5607 2022-09-03  12145.0
2022-09-10    Y_5607 2022-09-10  10686.0
...              ...        ...      ...
1939-05-20    Y_7270 1939-05-20      0.0
1939-05-27    Y_7270 1939-05-27      0.0
1939-06-03    Y_7270 1939-06-03      0.0
1939-06-10    Y_7270 1939-06-10      0.0
1939-06-17    Y_7270 1939-06-17      0.0

[129600 rows x 3 columns]

In [15]:
class FixedModelRNNProcessor:
    def __init__(self, dates=[]):
        self.dates = dates
        self.forecasts = []
        self.eval_pairs = []
        self.input_size = None
        self.nf = None
        self.config = None
        self.testset = None
        self.maes = []
        self.mses = []
        self.mapes = []
        self.nmses = []
        self.reference_dates = {}
        self.metrics_df = pd.DataFrame(columns=["Unique_id", "Reference Date", "MAE", "MSE", "MAPE", "NMSE"])
        self.display_df = pd.DataFrame(columns=["Unique_id", "Reference Date", "Target End Date", "GT", "Quantile", "Prediction"])
        self.selected_input_size = None

    def create_fixed_model(self, df_train, df_test, test_ids, h, freq, level=[]):
        input_length = df_train.groupby("unique_id").size().min()
        max_input_size = max(8, input_length - h - 1)
        self.testset = df_test

        def config(trial):
            return {
                "input_size": trial.suggest_int("input_size", 8, max_input_size),
                "encoder_hidden_size": trial.suggest_categorical("encoder_hidden_size", [32, 64, 128]),
                "encoder_n_layers": trial.suggest_int("encoder_n_layers", 1, 3),
                "context_size": trial.suggest_int("context_size", 1, h),
                "decoder_hidden_size": trial.suggest_categorical("decoder_hidden_size", [32, 64, 128]),
                "learning_rate": trial.suggest_float("learning_rate", 1e-4, 1e-2, log=True),
                "batch_size": trial.suggest_categorical("batch_size", [16, 32, 64]),
                "random_seed": trial.suggest_int("random_seed", 1, 99999),
                "start_padding_enabled": True,
                "accelerator": "gpu",
                "devices": 2,
                "strategy": "auto"
            }

        self.config = config

        if not level:
            nf = NeuralForecast(models=[AutoRNN(h=h, backend="optuna", config=self.config)], freq=freq)
        else:
            nf = NeuralForecast(models=[AutoRNN(h=h, backend="optuna", loss=MQLoss(level=level), config=self.config)], freq=freq)

        nf.fit(df=df_train)
        nf.save(path='./saved_models/RNN/',
                model_index=None,
                overwrite=True,
                save_dataset=True)
        self.nf = nf
        self.selected_input_size = nf.models[0].model.hparams['input_size']

        for uid in test_ids:
            series_df = df_test[df_test["unique_id"] == uid]
            if len(series_df) <= self.selected_input_size:
                print(f"Skipping {uid}: length {len(series_df)} < required {self.selected_input_size}")
                continue

            reference_date = series_df["ds"].iloc[-4]
            self.reference_dates[uid] = reference_date

            input_df = series_df[series_df["ds"] < reference_date]
            forecast = nf.predict(df=input_df).set_index("ds")
            forecast_horizon = forecast.index
            ground_truth = series_df[series_df["ds"].isin(forecast_horizon)].set_index("ds")

            self.forecasts.append(forecast)
            self.eval_pairs.append((forecast, ground_truth))
            self.dates.append(reference_date.strftime("%Y-%m-%d"))

    def calculate_metrics(self):
        for forecast_df, truth_df in self.eval_pairs:
            y_true = truth_df.iloc[:, 1].values
            y_pred = forecast_df.iloc[:, 1].values

            self.maes.append(mean_absolute_error(y_true, y_pred))
            self.mses.append(mean_squared_error(y_true, y_pred))
            self.mapes.append(mean_absolute_percentage_error(y_true, y_pred))
            self.nmses.append(self.mses[-1] / np.var(y_true))

    def create_metrics_df(self):
        for i in range(len(self.dates)):
            self.metrics_df.loc[len(self.metrics_df)] = [
                self.eval_pairs[i][0]["unique_id"].iloc[0],
                self.dates[i], self.maes[i], self.mses[i], self.mapes[i], self.nmses[i]
            ]

    def efficient_create_display_df(self):
        records = []
        testset_indexed = self.testset.set_index(["unique_id", "ds"])

        for forecast_df in tqdm(self.forecasts, desc="Building display_df"):
            uid = forecast_df["unique_id"].iloc[0]
            reference_date = self.reference_dates[uid]
            gt_series = testset_indexed.loc[uid]["y"] if uid in testset_indexed.index.get_level_values(0) else pd.Series()

            for col in forecast_df.columns:
                if col == "unique_id":
                    continue
                if "lo" in col:
                    number = int(col[-2:])
                    alpha = 1 - (number / 100)
                    quantile = alpha / 2
                elif "hi" in col:
                    number = int(col[-2:])
                    alpha = 1 - (number / 100)
                    quantile = 1 - (alpha / 2)
                elif col in ["AutoRNN-median", "AutoRNN"]:
                    quantile = 0.5
                else:
                    continue

                df_col = forecast_df[[col]].copy()
                df_col.rename(columns={col: "Prediction"}, inplace=True)
                df_col["Unique_id"] = uid
                df_col["Reference Date"] = reference_date
                df_col["Target End Date"] = df_col.index
                df_col["GT"] = df_col.index.map(gt_series.get)
                df_col["Quantile"] = quantile
                records.append(df_col)

        self.display_df = pd.concat(records)[["Unique_id", "Reference Date", "Target End Date", "GT", "Quantile", "Prediction"]]
        self.display_df.sort_values(by=["Unique_id", "Reference Date", "Target End Date", "Quantile"], inplace=True)
        self.display_df.reset_index(drop=True, inplace=True)

    def efficient_compute_wis(self):
        df = self.display_df.sort_values(by=["Unique_id", "Reference Date", "Target End Date", "Quantile"])
        results = []
        grouped = df.groupby(["Unique_id", "Reference Date", "Target End Date"])

        for (uid, ref_date, tgt_date), group in tqdm(grouped, desc="Computing WIS"):
            gt = group["GT"].iloc[0]
            group = group.sort_values("Quantile")
            if not np.any(np.isclose(group["Quantile"], 0.5)):
                continue
            median_pred = group[np.isclose(group["Quantile"], 0.5)]["Prediction"].iloc[0]
            ae = abs(median_pred - gt)
            lo = group[group["Quantile"] < 0.5]
            hi = group[group["Quantile"] > 0.5][::-1].reset_index(drop=True)

            wis_components = []
            for i in range(min(len(lo), len(hi))):
                alpha = hi.iloc[i]["Quantile"] - lo.iloc[i]["Quantile"]
                lo_pred, hi_pred = lo.iloc[i]["Prediction"], hi.iloc[i]["Prediction"]
                interval_score = (
                    hi_pred - lo_pred
                    + (2 / alpha) * (lo_pred - gt) * (gt < lo_pred)
                    + (2 / alpha) * (gt - hi_pred) * (gt > hi_pred)
                )
                wis_components.append(interval_score)

            wis = (ae + np.sum(wis_components)) / (1 + len(wis_components))
            results.append({
                "Unique_id": uid,
                "Reference Date": ref_date,
                "Target End Date": tgt_date,
                "GT": gt,
                "WIS": wis
            })

        return pd.DataFrame(results)

In [7]:
test_ids = [f"Y_{i}" for i in test_indices]

In [8]:
processor = FixedModelRNNProcessor()

In [9]:
processor.create_fixed_model(df_train, df_test_all, test_ids, h=4, freq="W-SAT", level = [10,20,30,40,50,60,70,80, 85,90,95])

[I 2026-02-06 18:55:41,235] A new study created in memory with name: no-name-ccebe056-9d31-4043-8387-962b98914c7e
[rank: 0] Seed set to 69356
/home/aa5dw/.local/lib/python3.12/site-packages/neuralforecast/models/rnn.py:170: UserWarning: context_size is deprecated and will be removed in future versions.
  warnings.warn(
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
💡 Tip: For seamless cloud logging and experiment tracking, try installing [litlogger](https://pypi.org/project/litlogger/) to enable LitLogger, which logs metrics and artifacts automatically to the Lightning Experiments platform.
Initializing distributed: GLOBAL_RANK: 0, MEMBER: 1/2
Initializing distributed: GLOBAL_RANK: 1, MEMBER: 2/2
----------------------------------------------------------------------------------------------------
distributed_backend=nccl
All distributed processes registered. Starting with 2 processes
-----------------------------------------------------------------------

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/home/aa5dw/.local/lib/python3.12/site-packages/pytorch_lightning/utilities/_pytree.py:21: `isinstance(treespec, LeafSpec)` is deprecated, use `isinstance(treespec, TreeSpec) and treespec.is_leaf()` instead.
/home/aa5dw/.local/lib/python3.12/site-packages/pytorch_lightning/utilities/_pytree.py:21: `isinstance(treespec, LeafSpec)` is deprecated, use `isinstance(treespec, TreeSpec) and treespec.is_leaf()` instead.


Training: |          | 0/? [00:00<?, ?it/s]

/home/aa5dw/.local/lib/python3.12/site-packages/torch/autograd/graph.py:865: UserWarning: The AccumulateGrad node's stream does not match the stream of the node that produced the incoming gradient. This may incur unnecessary synchronization and break CUDA graph capture if the AccumulateGrad node's stream is the default stream. This mismatch is caused by an AccumulateGrad node created prior to the current iteration being kept alive. This can happen if the autograd graph is still being kept alive by tensors such as the loss, or if you are using DDP, which will stash a reference to the node. To resolve the mismatch, delete all references to the autograd graph or ensure that DDP initialization is performed under the same stream as subsequent forwards. If the mismatch is intentional, you can use torch.autograd.graph.set_warn_on_accumulate_grad_stream_mismatch(False) to suppress this warning. (Triggered internally at /pytorch/torch/csrc/autograd/input_buffer.cpp:240.)
  return Variable._exec

...

Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
💡 Tip: For seamless cloud logging and experiment tracking, try installing [litlogger](https://pypi.org/project/litlogger/) to enable LitLogger, which logs metrics and artifacts automatically to the Lightning Experiments platform.
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]
/home/aa5dw/.local/lib/python3.12/site-packages/pytorch_lightning/utilities/_pytree.py:21: `isinstance(treespec, LeafSpec)` is deprecated, use `isinstance(treespec, TreeSpec) and treespec.is_leaf()` instead.


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
💡 Tip: For seamless cloud logging and experiment tracking, try installing [litlogger](https://pypi.org/project/litlogger/) to enable LitLogger, which logs metrics and artifacts automatically to the Lightning Experiments platform.
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0,1,2,3]
/home/aa5dw/.local/lib/python3.12/site-packages/pytorch_lightning/utilities/_pytree.py:21: `isinstance(treespec, LeafSpec)` is deprecated, use `isinstance(treespec, TreeSpec) and treespec.is_leaf()` instead.


Predicting: |          | 0/? [00:00<?, ?it/s]

In [10]:
display_df = processor.efficient_create_display_df()

Building display_df: 100%|██████████| 2160/2160 [01:17<00:00, 27.83it/s]


In [11]:
processor.display_df

Unique_id Reference Date Target End Date   GT  Quantile  Prediction
0            Y_1     2011-10-15      2011-10-15  0.0     0.025   -0.005509
1            Y_1     2011-10-15      2011-10-15  0.0     0.050   -0.002326
2            Y_1     2011-10-15      2011-10-15  0.0     0.075   -0.001542
3            Y_1     2011-10-15      2011-10-15  0.0     0.100   -0.001342
4            Y_1     2011-10-15      2011-10-15  0.0     0.150   -0.001265
...          ...            ...             ...  ...       ...         ...
198715    Y_9999     1957-03-02      1957-03-23  0.0     0.850    0.903615
198716    Y_9999     1957-03-02      1957-03-23  0.0     0.900    1.055019
198717    Y_9999     1957-03-02      1957-03-23  0.0     0.925    1.170734
198718    Y_9999     1957-03-02      1957-03-23  0.0     0.950    1.289846
198719    Y_9999     1957-03-02      1957-03-23  0.0     0.975    2.165518

[198720 rows x 6 columns]

In [12]:
processor.display_df.to_csv('../../output/forecasts_RNN.csv',index=None)

In [13]:
wis_table = processor.efficient_compute_wis()

Computing WIS: 100%|██████████| 8640/8640 [00:27<00:00, 315.52it/s]


In [14]:
wis_table

Unique_id Reference Date Target End Date   GT       WIS
0          Y_1     2011-10-15      2011-10-15  0.0  0.004714
1          Y_1     2011-10-15      2011-10-22  0.0  0.002970
2          Y_1     2011-10-15      2011-10-29  0.0  0.001693
3          Y_1     2011-10-15      2011-11-05  0.0  0.001239
4       Y_1000     2022-06-11      2022-06-11  0.0  0.171434
...        ...            ...             ...  ...       ...
8635    Y_9998     1955-03-26      1955-04-16  0.0  1.004370
8636    Y_9999     1957-03-02      1957-03-02  0.0  3.639038
8637    Y_9999     1957-03-02      1957-03-09  0.0  4.386145
8638    Y_9999     1957-03-02      1957-03-16  0.0  4.908896
8639    Y_9999     1957-03-02      1957-03-23  0.0  3.304841

[8640 rows x 5 columns]

In [15]:
np.mean(wis_table['WIS'].values)

np.float64(140.09106511237516)

In [16]:
wis_dfs = [wis_table.iloc[i::4].reset_index(drop=True) for i in range(4)]

In [17]:
np.mean(wis_dfs[3]['WIS'].values)

np.float64(57.72690760440222)

In [18]:
wis_table.to_csv('../../eval/WIS_RNN.csv')